# ML Pipeline Preparation
Follow the instructions below to help you create your ML pipeline.
### 1. Import libraries and load data from database.
- Import Python libraries
- Load dataset from database with [`read_sql_table`](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.read_sql_table.html)
- Define feature and target variables X and Y

In [1]:
# import libraries
import pandas as pd
from sqlalchemy import create_engine

import re
import nltk

from nltk.corpus import stopwords
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.tokenize import word_tokenize
from nltk.tokenize.casual import TweetTokenizer

from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.multioutput import MultiOutputClassifier
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from sklearn.model_selection import GridSearchCV

In [2]:
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


True

In [3]:
# load data from database
engine = create_engine('sqlite:///InsertDatabaseName.db')
df = pd.read_sql_table('InsertTableName', engine)
categories = ['related', 'request', 'offer', 'aid_related', 'medical_help', 'medical_products', 'search_and_rescue', 'security', 'military', 'child_alone', 'water', 'food', 'shelter', 'clothing', 'money', 'missing_people', 'refugees', 'death', 'other_aid', 'infrastructure_related', 'transport', 'buildings', 'electricity', 'tools', 'hospitals', 'shops', 'aid_centers', 'other_infrastructure', 'weather_related', 'floods', 'storm', 'fire', 'earthquake', 'cold', 'other_weather', 'direct_report']
X = df['message']
Y = df[categories]

2

### 2. Write a tokenization function to process your text data

In [4]:
url_regex = 'http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+'

def tokenize(text):
    
    urls = re.findall(url_regex, text)
    for url in urls:
        text.replace(url, 'linktext')
   
    #TODO remove punctuation
    text = re.sub(r"[^a-zA-Z0-9]", " ",text)
    #TODO remove stopwords
    stop_words = stopwords.words("english")
    lemmatizer = WordNetLemmatizer()
    #TODO tokenize sentences
    #sentences = sent_tokenize(text)
    #Tweet Tokenizer?
    #words = word_tokenize(text)
    tokenizer = TweetTokenizer(preserve_case=False, strip_handles=True)
    words= tokenizer.tokenize(text)
    cleaned_lemmed_list = []
    for word in words: 
        if word not in stop_words:
            cleaned_lemmed_word = lemmatizer.lemmatize(word).lower().strip()
            cleaned_lemmed_list.append(cleaned_lemmed_word)
    return cleaned_lemmed_list
    #pass

In [5]:
X.apply(tokenize)

0        [weather, update, cold, front, cuba, could, pa...
1                                              [hurricane]
2                                 [looking, someone, name]
3        [un, report, leogane, 80, 90, destroyed, hospi...
4        [say, west, side, haiti, rest, country, today,...
5                          [information, national, palace]
6                            [storm, sacred, heart, jesus]
7                 [please, need, tent, water, silo, thank]
8                   [would, like, receive, message, thank]
9        [croix, de, bouquet, health, issue, worker, sa...
10                [nothing, eat, water, starving, thirsty]
11       [petionville, need, information, regarding, 4636]
12       [thomassin, number, 32, area, named, pyron, wo...
13       [let, together, need, food, delma, 75, didine,...
14       [information, 4636, number, order, participate...
15       [comitee, delmas, 19, rue, street, janvier, im...
16       [need, food, water, klecin, 12, dying, hunger,.

### 3. Build a machine learning pipeline
This machine pipeline should take in the `message` column as input and output classification results on the other 36 categories in the dataset. You may find the [MultiOutputClassifier](http://scikit-learn.org/stable/modules/generated/sklearn.multioutput.MultiOutputClassifier.html) helpful for predicting multiple target variables.

In [5]:
pipeline = Pipeline([
            ('vect', CountVectorizer(tokenizer=tokenize)),
            ('tfidf', TfidfTransformer()),
            ('clf', MultiOutputClassifier(estimator = RandomForestClassifier(), ))
        ])

### 4. Train pipeline
- Split data into train and test sets
- Train pipeline

In [6]:
X_train, X_test, y_train, y_test = train_test_split(X, Y)

In [19]:

pipeline.fit(X_train, y_train)

Pipeline(memory=None,
     steps=[('vect', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=1,
        ngram_range=(1, 1), preprocessor=None, stop_words=None,
        strip...oob_score=False, random_state=None, verbose=0,
            warm_start=False),
           n_jobs=1))])

### 5. Test your model
Report the f1 score, precision and recall for each output category of the dataset. You can do this by iterating through the columns and calling sklearn's `classification_report` on each.

In [69]:
y_pred = pipeline.predict(X_test)



In [43]:
print("y_test {} \n shape {} \n y_pred {} \n shape {}".format(y_test,y_test.shape,y_pred,y_pred.shape))

y_test        related  request  offer  aid_related  medical_help  medical_products  \
10657        1        0      0            1             0                 0   
2283         1        0      0            1             0                 0   
17982        1        0      0            1             0                 0   
1791         1        0      0            1             0                 0   
6186         1        0      0            1             0                 0   
15080        1        0      0            1             0                 0   
277          1        0      0            1             0                 0   
7245         1        0      0            0             0                 0   
15086        1        0      0            1             0                 0   
3252         1        0      0            0             0                 0   
14487        1        0      0            1             0                 0   
21129        0        0      0            0  

In [39]:
df_yp = pd.DataFrame(y_pred)
df_yt = pd.DataFrame(y_test)

In [32]:
y_true = y_test.values

In [85]:
#for truth, prediction in np.ndindex(y_true), np.ndindex(y_pred):
in_out = ['Not cat', 'cat']
for cat in np.arange(0, 36):
    print ('Score for {}:\n{}'.format(categories[cat],classification_report(y_true[cat], y_pred[cat],target_names = in_out)))
    
#for truth, prediction in np.ndindex(y_true), np.ndindex(y_pred)
    #print(classification_report(truth, prediction))
#print(classification_report(y_test, y_pred, target_names=categories))
#print(classification_report(df_yt, df_yp, target_names=df_yt.columns))
#temp_cat=list('abcdefghijklmnopqrstuvwxyzABCDEFGHIJ')
#print(classification_report(y_test, y_pred))
#temp_cat
#print(classification_report(y_true, y_pred, target_names=categories))
#import numpy as np
#Y_pred = np.squeeze(pipeline.predict(X_test[0:5]))
#threshold = 0.5
#classification_report(y_true[0:5], Y_pred > threshold, target_names=categories )
#print(classification_report(y_true, y_pred, target_names=in_out))

ValueError: Unknown label type: (array([[1, 0, 0, ..., 0, 0, 1],
       [1, 0, 0, ..., 0, 1, 1],
       [1, 0, 0, ..., 0, 0, 0],
       ..., 
       [1, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [1, 0, 0, ..., 0, 0, 0]]), array([[1, 0, 0, ..., 0, 0, 0],
       [1, 0, 0, ..., 0, 0, 0],
       [1, 0, 0, ..., 0, 0, 0],
       ..., 
       [1, 0, 0, ..., 0, 0, 0],
       [1, 0, 0, ..., 0, 0, 0],
       [1, 0, 0, ..., 0, 0, 0]]))

In [48]:
y_true = [0, 1, 2, 2, 2]
y_pred = [0, 0, 2, 2, 1]
target_names = ['class 0', 'class 1', 'class 2']
print(classification_report(y_true, y_pred, target_names=target_names))

             precision    recall  f1-score   support

    class 0       0.50      1.00      0.67         1
    class 1       0.00      0.00      0.00         1
    class 2       1.00      0.67      0.80         3

avg / total       0.70      0.60      0.61         5



### 6. Improve your model
Use grid search to find better parameters. 

In [13]:
pipeline.get_params()

{'memory': None,
 'steps': [('vect',
   CountVectorizer(analyzer='word', binary=False, decode_error='strict',
           dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
           lowercase=True, max_df=1.0, max_features=None, min_df=1,
           ngram_range=(1, 1), preprocessor=None, stop_words=None,
           strip_accents=None, token_pattern='(?u)\\b\\w\\w+\\b',
           tokenizer=<function tokenize at 0x7f4982875598>, vocabulary=None)),
  ('tfidf',
   TfidfTransformer(norm='l2', smooth_idf=True, sublinear_tf=False, use_idf=True)),
  ('clf',
   MultiOutputClassifier(estimator=RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
               max_depth=None, max_features='auto', max_leaf_nodes=None,
               min_impurity_decrease=0.0, min_impurity_split=None,
               min_samples_leaf=1, min_samples_split=2,
               min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=1,
               oob_score=False, random_state=None,

In [53]:
from sklearn.metrics import make_scorer
parameters = {
        #'features__text_pipeline__vect__ngram_range': ((1, 1), (1, 2)),
        #'features__text_pipeline__vect__max_df': (0.5, 0.75, 1.0),
        #'features__text_pipeline__vect__max_features': (None, 5000, 10000),
        #'features__text_pipeline__tfidf__use_idf': (True, False),
        #'clf__estimator__n_estimators': [50, 100, 200],
        'clf__estimator__min_samples_split': [2, 3],
        #'features__transformer_weights': (
            #{'text_pipeline': 1, 'starting_verb': 0.5},
            #{'text_pipeline': 0.5, 'starting_verb': 1},
            #{'text_pipeline': 0.8, 'starting_verb': 1},
        #)
    }
scorer = make_scorer(recall_score)
cv = GridSearchCV(pipeline, scoring = scorer, param_grid=parameters)

### 7. Test your model
Show the accuracy, precision, and recall of the tuned model.  

Since this project focuses on code quality, process, and  pipelines, there is no minimum performance metric needed to pass. However, make sure to fine tune your models for accuracy, precision and recall to make your project stand out - especially for your portfolio!

In [54]:
gs = cv.fit(X_train, y_train)



Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO nam

ValueError: multiclass-multioutput is not supported

In [25]:
gs.score(X_test, y_test)

0.23787000305157155

In [55]:
best = gs.best_estimator_

In [61]:
bp = best.predict(X_test)

Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO name='/root/nltk_data/corpora/stopwords/english' mode='rb' closefd=True>
Exception ignored in: <_io.FileIO nam

In [57]:
y_true = y_test.values

In [62]:
import numpy as np
from sklearn.metrics import accuracy_score, precision_score, recall_score
import warnings
#https://stackoverflow.com/questions/5644836/in-python-how-does-one-catch-warnings-as-if-they-were-exceptions
warnings.filterwarnings("error")
acc_list = []
pre_list = []
rec_list = []
for cat in np.arange(0, 36):
    acc_list.append(accuracy_score(y_true[cat], bp[cat]))
    try:
        pre_list.append(precision_score(y_true[cat],bp[cat]))
        rec_list.append(recall_score(y_true[cat],bp[cat]))
    except: 
        #UndefnedMetricWarning:
        pre_list.append(np.nan)
        rec_list.append(np.nan)       
#print(np.mean(acc_list))
#print(np.nanmean(pre_list))
#print(np.nanmean(rec_list))
print('Accuracy: {}'.format(np.mean(acc_list)))
print('Precision: {}'.format(np.nanmean(pre_list)))
print('Recall: {}'.format(np.nanmean(rec_list)))
print(rec_list)

Accuracy: 0.9544753086419752
Precision: 0.7854166666666667
Recall: 0.5867857142857142
[0.625, 1.0, 0.42857142857142855, 0.40000000000000002, 1.0, 0.5, nan, nan, 0.5, 0.0, 0.59999999999999998, 1.0, 0.5, nan, 0.5, nan, 0.0, 1.0, 0.5, 0.75, 1.0, 0.33333333333333331, 1.0, 0.5, 0.33333333333333331, 0.42857142857142855, nan, 0.80000000000000004, 0.59999999999999998, 0.40000000000000002, 0.33333333333333331, 0.5714285714285714, 1.0, nan, 0.0, 1.0]


In [11]:
from sklearn.metrics import accuracy_score, precision_score, recall_score
#https://stackoverflow.com/questions/38697982/python-scikit-learn-multi-class-multi-label-performance-metrics
print('Accuracy: {}'.format(accuracy_score(y_test[:, 0], bp[:, 0])))
#print('Precision: {}'.format(precision_score(y_test,bp)))
#print('Recall: {}'.format(recall_score(y_test,bp)))

TypeError: unhashable type: 'slice'

In [50]:
from sklearn.metrics import confusion_matrix

confusion_matrix(y_true, bp)

ValueError: multiclass-multioutput is not supported

In [42]:
yt = pd.DataFrame(y_test)
y_tru = pd.DataFrame(yt.values)
y_truth = pd.DataFrame(y_tru.iloc[:, 0])
b_pred = pd.DataFrame(bp[:, 0])
accuracy_score(y_truth, b_pred)
#b_pred
#y_truth
#accuracy_score(yt, bp[:, 0])

0.80042722001830946

### 8. Try improving your model further. Here are a few ideas:
* try other machine learning algorithms
* add other features besides the TF-IDF

In [24]:
that_list = [[1,3], [8,np.nan]]
import numpy as np
np.nanmean(that_list)

4.0

### 9. Export your model as a pickle file

In [48]:
import pickle
pickle_file = open('model_save', 'wb')
pickle.dump(best, pickle_file)
pickle_file.close()

### 10. Use this notebook to complete `train.py`
Use the template file attached in the Resources folder to write a script that runs the steps above to create a database and export a model based on a new dataset specified by the user.